In [27]:
from xgboost import XGBClassifier
import pandas as pd
import numpy as np
import pickle
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [28]:
!cat models/20192009_5/train.csv | wc -l

41000


In [29]:
!ls models/20192009_5/

train-data-10_4.csv  train-data-1_9.csv   train-data-3_1.csv
train-data-17_3.csv  train-data-21_3.csv  train-data-40_2.csv
train-data-19_2.csv  train-data-21_4.csv  train-data-5_5.csv
train-data-1_3.csv   train-data-2_4.csv   train-data-6_1.csv
train-data-1_4.csv   train-data-30_3.csv  train.csv
train-data-1_5.csv   train-data-31_6.csv
train-data-1_6.csv   train-data-33_5.csv


In [30]:
features = ["f" + str(i) for i in range(0,57)]
label = ["action"]

headers = features + label

df = pd.read_csv('models/20192009_5/train.csv', 
                 sep = ',', 
                 header = None,
                 names = headers)
df

f0  f1  f2   f3   f4   f5   f6  f7  f8  f9  ...  f48  f49  f50  f51  \
0      232   2   5  694 -165  674  397 -84  -1   7  ...  381  -92    2    2   
1      224   2   5  692 -175  669  399 -79  -1   7  ...  379  -87    2    2   
2      224   2   5  687 -177  664  401 -74  -1   7  ...  377  -82    2    2   
3      232   2   5  681 -171  659  403 -69  -1   7  ...  375  -77    2    2   
4      232   2   5  676 -173  654  405 -64  -1   7  ...  373  -72    2    2   
...    ...  ..  ..  ...  ...  ...  ...  ..  ..  ..  ...  ...  ...  ...  ...   
40995  217   0   1  582 -218  540  435  50   1   5  ...   70   68    0    1   
40996  217   0   1  581 -218  539  435  51   1   5  ...   72   75    0    1   
40997  217   0   1  580 -218  538  435  52   1   5  ...   74   82    0    1   
40998  217   0   1  580 -218  537  435  53   1   5  ...   76   89    0    1   
40999  217   0   1  579 -218  536  435  54   1   5  ...   78   96    0    1   

       f52  f53  f54  f55  f56  action  
0      687  -28  686  260  -96       0  
1      685  -38  684  262  -94       0  
2      683  -40  682  264  -92       2  
3      681  -34  680  266  -90       1  
4      679  -36  678  268  -88       5  
...    ...  ...  ...  ...  ...     ...  
40995  669 -166  648  383  -58       3  
40996  668 -166  647  383  -57       3  
40997  667 -166  646  383  -56       3  
40998  666 -166  645  383  -55       3  
40999  665 -166  644  383  -54       3  

[41000 rows x 58 columns]

In [31]:
print("headers length: {}, df lenght: {}".format(len(headers), len(df)))

headers length: 58, df lenght: 41000


In [32]:
df["f0"].value_counts()

168    1469
136    1436
200    1410
144    1401
152    1360
       ... 
449       2
329       2
345       2
441       1
433       1
Name: f0, Length: 161, dtype: int64

In [33]:
print("different actions count \n{}".format(df.drop_duplicates()['action'].value_counts()))

different actions count 
3    7863
0    7160
5    6923
1    6597
2    6281
4    6176
Name: action, dtype: int64


In [34]:
print("no of states without duplicates: {}".format(len(df.drop_duplicates())))

no of states without duplicates: 41000


In [35]:
y_train_all = df["action"]
X_train_all = df.drop(columns="action")

In [36]:
print("no of states without duplicates and action column: {}".format(len(X_train_all.drop_duplicates())))

no of states without duplicates and action column: 41000


In [38]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

In [12]:
# X_train_all[["f0", "f1"]]

In [39]:
def evaluate_model(xtrain, ytrain, xtest, ytest, model):
    y_pred_test = model.predict(xtest)
    y_pred_train = model.predict(xtrain)
    test_accuracy = accuracy_score(ytest, y_pred_test)
    train_accuracy = accuracy_score(ytrain, y_pred_train)
    print('Training accuracy: {0:.2f}, evaluation accuracy: {1:.2f}'.format(train_accuracy, test_accuracy))


Basic logisting regresion

In [40]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, test_size=0.2)

classifier = LogisticRegression().fit(X_train, y_train)

In [41]:
evaluate_model(X_train, y_train, X_test, y_test, classifier)

Training accuracy: 0.25, evaluation accuracy: 0.24


In [42]:
pickle.dump(classifier, open("ai_model_logit.pkl","wb"))

xgboost

In [43]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, 
                                                    test_size=0.2, random_state=7)

xgb_model = XGBClassifier(n_estimators=500).fit(X_train, y_train,eval_set = [[X_test, y_test]], verbose = 1)

[0]	validation_0-merror:0.743659
[1]	validation_0-merror:0.74561
[2]	validation_0-merror:0.743902
[3]	validation_0-merror:0.745366
[4]	validation_0-merror:0.743902
[5]	validation_0-merror:0.739756
[6]	validation_0-merror:0.74061
[7]	validation_0-merror:0.738659
[8]	validation_0-merror:0.741951
[9]	validation_0-merror:0.74
[10]	validation_0-merror:0.739756
[11]	validation_0-merror:0.737439
[12]	validation_0-merror:0.739146
[13]	validation_0-merror:0.737317
[14]	validation_0-merror:0.738415
[15]	validation_0-merror:0.736951
[16]	validation_0-merror:0.735122
[17]	validation_0-merror:0.734756
[18]	validation_0-merror:0.735
[19]	validation_0-merror:0.733415
[20]	validation_0-merror:0.733293
[21]	validation_0-merror:0.733415
[22]	validation_0-merror:0.732561
[23]	validation_0-merror:0.733781
[24]	validation_0-merror:0.732683
[25]	validation_0-merror:0.733293
[26]	validation_0-merror:0.732561
[27]	validation_0-merror:0.732927
[28]	validation_0-merror:0.732561
[29]	validation_0-merror:0.730244

[238]	validation_0-merror:0.702683
[239]	validation_0-merror:0.701707
[240]	validation_0-merror:0.701829
[241]	validation_0-merror:0.701463
[242]	validation_0-merror:0.700976
[243]	validation_0-merror:0.700854
[244]	validation_0-merror:0.701219
[245]	validation_0-merror:0.701829
[246]	validation_0-merror:0.701707
[247]	validation_0-merror:0.702195
[248]	validation_0-merror:0.702195
[249]	validation_0-merror:0.702195
[250]	validation_0-merror:0.703537
[251]	validation_0-merror:0.702317
[252]	validation_0-merror:0.701829
[253]	validation_0-merror:0.702561
[254]	validation_0-merror:0.701707
[255]	validation_0-merror:0.702317
[256]	validation_0-merror:0.701829
[257]	validation_0-merror:0.701829
[258]	validation_0-merror:0.701341
[259]	validation_0-merror:0.700732
[260]	validation_0-merror:0.700122
[261]	validation_0-merror:0.70061
[262]	validation_0-merror:0.700854
[263]	validation_0-merror:0.700122
[264]	validation_0-merror:0.701098
[265]	validation_0-merror:0.701585
[266]	validation_0-me

[474]	validation_0-merror:0.696463
[475]	validation_0-merror:0.696463
[476]	validation_0-merror:0.695854
[477]	validation_0-merror:0.696585
[478]	validation_0-merror:0.696098
[479]	validation_0-merror:0.696463
[480]	validation_0-merror:0.696098
[481]	validation_0-merror:0.696098
[482]	validation_0-merror:0.695854
[483]	validation_0-merror:0.695488
[484]	validation_0-merror:0.695488
[485]	validation_0-merror:0.694756
[486]	validation_0-merror:0.694878
[487]	validation_0-merror:0.694268
[488]	validation_0-merror:0.693902
[489]	validation_0-merror:0.69439
[490]	validation_0-merror:0.694146
[491]	validation_0-merror:0.694268
[492]	validation_0-merror:0.694146
[493]	validation_0-merror:0.694024
[494]	validation_0-merror:0.694512
[495]	validation_0-merror:0.694878
[496]	validation_0-merror:0.69439
[497]	validation_0-merror:0.694512
[498]	validation_0-merror:0.69439
[499]	validation_0-merror:0.694634


In [44]:
evaluate_model(X_train, y_train, X_test, y_test, xgb_model)

Training accuracy: 0.45, evaluation accuracy: 0.31


In [45]:
xgb_model = XGBClassifier(n_estimators=500).fit(X_train_all, y_train_all)

In [46]:
pickle.dump(xgb_model, open("ai_model_xgb.pkl","wb"))

random forest model

In [21]:
forest_model = RandomForestClassifier(random_state=1, n_estimators=500)
forest_model.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=500,
                       n_jobs=None, oob_score=False, random_state=1, verbose=0,
                       warm_start=False)

In [22]:
evaluate_model(X_train, y_train, X_test, y_test, forest_model)

Training accuracy: 1.00, evaluation accuracy: 0.23


In [ ]:
# min_max_scaler = MinMaxScaler()
# np_scaled = min_max_scaler.fit_transform(df)
# df_normalized = pd.DataFrame(np_scaled)
# df_normalized.columns = feature_cols + ['Class']

In [ ]:
# def make_crosses(X_train, X_validation, degree=2):
#   from sklearn.preprocessing import PolynomialFeatures
#   poly = PolynomialFeatures(degree=degree)
#   X_train_poly = poly.fit_transform(X_train)
#   X_validation_poly = poly.transform(X_validation)
#   return X_train_poly, X_validation_poly

In [47]:
mlp_model = MLPClassifier(solver='lbfgs', alpha=1e-5, 
                    hidden_layer_sizes=(24, 24), random_state=1, max_iter=200000)

mlp_model.fit(X_train_all, y_train_all)

MLPClassifier(activation='relu', alpha=1e-05, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(24, 24), learning_rate='constant',
              learning_rate_init=0.001, max_iter=200000, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=1, shuffle=True, solver='lbfgs', tol=0.0001,
              validation_fraction=0.1, verbose=False, warm_start=False)

In [48]:
evaluate_model(X_train, y_train, X_test, y_test, mlp_model)

Training accuracy: 0.15, evaluation accuracy: 0.16


Save models to pkl

In [25]:
pickle.dump(forest_model, open("ai_model_forest.pkl","wb"))

OSError: [Errno 22] Invalid argument

In [49]:
pickle.dump(mlp_model, open("ai_model_mlp.pkl","wb"))

In [ ]:
!ls

In [ ]:
# model_p = pickle.load(open("ai_model.pkl","rb"))
game_state_4f = (np.array([8,280,630,-1,1,674,-3,7,667,-1,2,649,-3,2,662,0,3,662,-1,4,655,-1,5,608,2,7,1,8,288,630,-1,1,672,-3,7,668,-1,2,650,-3,2,661,0,3,657,-1,4,649,-1,5,602,2,7,1,8,296,629,-1,1,670,-3,7,669,-1,2,651,-3,2,660,0,3,651,-1,4,643,-1,5,596,2,7,1,8,296,628,-1,1,665,-3,7,667,-1,2,650,-3,2,658,0,3,647,-1,4,638,-1,5,589,2,7])
                 .reshape(1, -1))



game_state_1f = (np.array([25, -410, 308, 5, 1, -343, 483, 1, 2, -417, 592, 5, 2, -184, 589, 1, 2, -222, 275, 7, 2, -93, 143, 3, -2, -128, 549, 1, -3, -121, 399, 6, -3]).reshape(1, -1))

xgb_model.predict(game_state_1f)